### Load Necessary Packages

In [1]:
import pandas as pd
import numpy as np
import os
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import mean_squared_error
from sklearn.neighbors import NearestNeighbors
from sklearn.preprocessing import StandardScaler

### Load Data

In [2]:
# Paths to the folders containing the CSV files
practice_folder = 'D://ACIC//practice'  
practice_year_folder = 'D://ACIC//practice_year'  
output_folder = 'D://ACIC//output' 

### Merge Data

In [ ]:
# Function to merge files
def merge_files(index):
    practice_file = f'{practice_folder}/acic_practice_{index:04d}.csv'
    practice_year_file = f'{practice_year_folder}/acic_practice_year_{index:04d}.csv'
    df_practice = pd.read_csv(practice_file)
    df_practice_year = pd.read_csv(practice_year_file)
    df_merged = pd.merge(df_practice, df_practice_year, on='id.practice')
    output_file = f'{output_folder}/merged_{index:04d}.csv'
    df_merged.to_csv(output_file, index=False)

# Loop through all file indices and merge
for i in range(1, 3401):
    merge_files(i)

print("Merging completed.")

### The linear Regression built previously (Wrong Assumption)
we need to calculate the treatment effect, which is using the Observed outcome after treatment Yit(1) - the outcome 
before treatment Yit(0) at the time t(which means post=1, year 3 and year 4), it means the data is in the treated group(Z=1). Here is basically we build a model based on before treatment data(year 1 & year 2), and then use the model to predict data without treatment effect on year 3 and year 4(to get Yit(0)).

In [3]:
# Function to estimate SATT using linear regression
def estimate_satt_linear(index):
    merged_file = f'{output_folder}/merged_{index:04d}.csv'
    df = pd.read_csv(merged_file)
    df = pd.get_dummies(df, columns=['X2', 'X4'], drop_first=True)
    
    # Define feature matrix X and target variable y for pre-intervention period
    pre_df = df[df['post'] == 0]
    X_pre = pre_df.drop(columns=['Y', 'id.practice', 'year', 'Z', 'post'])
    y_pre = pre_df['Y']
    
    # Train model on pre-intervention data
    model_pre = LinearRegression().fit(X_pre, y_pre)
    
    # Define feature matrix X for post-intervention period
    post_df = df[df['post'] == 1]
    X_post = post_df.drop(columns=['Y', 'id.practice', 'year', 'Z', 'post'])
    
    # Predict counterfactual outcomes for post-intervention period
    post_df['Y_pred_control'] = model_pre.predict(X_post)
    
    # Calculate the treatment effect: Yit(1) - Yit(0)
    post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
    
    # Filter for treated practices
    treated_post_df = post_df[post_df['Z'] == 1]
    
    # Weight the treatment effects by the number of patients
    weighted_sum = (treated_post_df['n.patients'] * treated_post_df['treatment_effect']).sum()
    total_patients = treated_post_df['n.patients'].sum()
    
    satt = weighted_sum / total_patients if total_patients > 0 else np.nan
    
    return {'index': index, 'satt': satt}

# Loop through all merged files and estimate SATT
results = []
for i in range(1, 3401):
    result = estimate_satt_linear(i)
    results.append(result)

# Save results
rmse_df = pd.DataFrame(results)
rmse_df.to_csv(f'{output_folder}/rmse_results.csv', index=False)

print("Model development and RMSE calculation completed.")


C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

...

C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

Model development and RMSE calculation completed.


C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['Y_pred_control'] = model_pre.predict(X_post)
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  post_df['treatment_effect'] = post_df['Y'] - post_df['Y_pred_control']
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3880981364.py:20: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Data

In [4]:
# Load your estimates
estimates_file_path = 'D:/ACIC/output/rmse_results.csv'
estimates_df = pd.read_csv(estimates_file_path)

# Rename columns for clarity
estimates_df.rename(columns={'index': 'dataset.num', 'satt': 'estimated_SATT'}, inplace=True)

# Load the truth file
truths_file_path = 'D:/ACIC/ACIC_estimand_truths.csv'
truths_df = pd.read_csv(truths_file_path)

# Filter to get only the overall SATTs for each dataset
overall_truths_df = truths_df[truths_df['variable'] == 'Overall']

# Merge the estimates with the overall truths
merged_df = pd.merge(estimates_df, overall_truths_df, on='dataset.num')

# Compute the squared error and RMSE
merged_df['squared_error'] = (merged_df['estimated_SATT'] - merged_df['SATT']) ** 2
rmse = np.sqrt(merged_df['squared_error'].mean())

print(f'Overall RMSE: {rmse}')

Overall RMSE: 326.3566065857506


### Propensity Score Matching

In [5]:
# Function to estimate SATT using propensity score matching
def estimate_satt_psm(index):
    merged_file = f'{output_folder}/merged_{index:04d}.csv'
    df = pd.read_csv(merged_file)
    
    # Filter for Year 2 (pre) and Year 3 (post)
    df = df[df['year'].isin([2, 3])]
    
    # One-hot encode categorical variables
    df = pd.get_dummies(df, columns=['X2', 'X4'], drop_first=True)
    
    # Define feature matrix X and treatment indicator Z
    X = df.drop(columns=['Y', 'id.practice', 'year', 'Z', 'post'])
    Z = df['Z']
    
    # Estimate propensity scores using logistic regression
    prop_model = LogisticRegression().fit(X, Z)
    df['propensity_score'] = prop_model.predict_proba(X)[:, 1]
    
    # Split into treated and control groups
    treated = df[df['Z'] == 1]
    control = df[df['Z'] == 0]
    
    # Perform matching (nearest neighbor matching)
    nn = NearestNeighbors(n_neighbors=1)
    nn.fit(control[['propensity_score']])
    distances, indices = nn.kneighbors(treated[['propensity_score']])
    
    matched_control = control.iloc[indices.flatten()].copy()
    
    # Calculate the treatment effect: Yit(1) - Yit(0)
    treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
    
    # Weight the treatment effects by the number of patients
    weighted_sum = (treated['n.patients'] * treated['treatment_effect']).sum()
    total_patients = treated['n.patients'].sum()
    
    satt = weighted_sum / total_patients if total_patients > 0 else np.nan
    
    return {'index': index, 'satt': satt}

# Loop through all merged files and estimate SATT using PSM
results_psm = []
for i in range(1, 3401):
    result = estimate_satt_psm(i)
    results_psm.append(result)

# Save results
psm_df = pd.DataFrame(results_psm)
psm_df.to_csv(f'{output_folder}/results_psm.csv', index=False)

print("PSM model development and SATT estimation completed.")

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

...

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

PSM model development and SATT estimation completed.


C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\AppData\Local\Temp\ipykernel_2984\3292461456.py:32: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  treated['treatment_effect'] = treated['Y'].values - matched_control['Y'].values
C:\Users\Jensen R\anaconda3\Lib\site-packag

In [6]:
# Load your estimates
estimates_file_path = 'D:/ACIC/output/rmse_results_psm.csv'
estimates_df = pd.read_csv(estimates_file_path)

# Rename columns for clarity
estimates_df.rename(columns={'index': 'dataset.num', 'satt': 'estimated_SATT'}, inplace=True)

# Load the truth file
truths_file_path = 'D:/ACIC/ACIC_estimand_truths.csv'
truths_df = pd.read_csv(truths_file_path)

# Filter to get only the year 3 SATTs for each dataset
yearly_truths_df = truths_df[(truths_df['variable']=='Yearly')&(truths_df['year'] == 3)]

# Merge the estimates with the year 3 truths
merged_df = pd.merge(estimates_df, yearly_truths_df, on='dataset.num')

# Compute the squared error and RMSE
merged_df['squared_error'] = (merged_df['estimated_SATT'] - merged_df['SATT']) ** 2
rmse = np.sqrt(merged_df['squared_error'].mean())

print(f'Overall RMSE: {rmse}')

Overall RMSE: 55.89634711476482


### Propensity Score Stratification

In [7]:
# Function to estimate SATT using propensity score stratification for specific years
def estimate_satt_stratification(index):
    merged_file = f'{output_folder}/merged_{index:04d}.csv'
    df = pd.read_csv(merged_file)
    
    # Filter for Year 2 (pre) and Year 3 (post)
    pre_df = df[(df['post'] == 0) & (df['year'] == 2)]
    post_df = df[(df['post'] == 1) & (df['year'] == 3)]
    
    # Combine pre and post data
    combined_df = pd.concat([pre_df, post_df], ignore_index=True)
    
    # One-hot encode categorical variables
    combined_df = pd.get_dummies(combined_df, columns=['X2', 'X4'], drop_first=True)
    
    # Define feature matrix X and treatment indicator Z
    X = combined_df.drop(columns=['Y', 'id.practice', 'year', 'Z', 'post'])
    Z = combined_df['Z']
    
    # Estimate propensity scores using logistic regression
    prop_model = LogisticRegression().fit(X, Z)
    combined_df['propensity_score'] = prop_model.predict_proba(X)[:, 1]
    
    # Stratify into quantiles
    combined_df['strata'] = pd.qcut(combined_df['propensity_score'], q=5, labels=False)
    
    # Calculate treatment effects within each stratum
    total_treatment_effect = 0
    total_count = 0
    for stratum in combined_df['strata'].unique():
        stratum_df = combined_df[combined_df['strata'] == stratum]
        treated_stratum = stratum_df[stratum_df['Z'] == 1]
        control_stratum = stratum_df[stratum_df['Z'] == 0]
        
        if len(treated_stratum) > 0 and len(control_stratum) > 0:
            treatment_effect_stratum = treated_stratum['Y'].mean() - control_stratum['Y'].mean()
            total_treatment_effect += treatment_effect_stratum * len(treated_stratum)
            total_count += len(treated_stratum)
    
    satt = total_treatment_effect / total_count if total_count > 0 else np.nan
    
    return {'index': index, 'satt': satt}

output_folder = 'D:/ACIC/output'  # Update with your desired output path

# Ensure the output folder exists
os.makedirs(output_folder, exist_ok=True)

# Loop through all merged files and estimate SATT using stratification
results = []
for i in range(1, 3401):
    result = estimate_satt_stratification(i)
    results.append(result)

# Save results
results_df = pd.DataFrame(results)
results_df.to_csv(f'{output_folder}/results_stratification.csv', index=False)

print("Stratification model development and SATT estimation completed.")

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

...

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

Stratification model development and SATT estimation completed.


C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(
C:\Users\Jensen R\anaconda3\Lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n

In [8]:
# Load your estimates
estimates_file_path = 'D:/ACIC/output/results_stratification.csv'
estimates_df = pd.read_csv(estimates_file_path)

# Rename columns for clarity
estimates_df.rename(columns={'index': 'dataset.num', 'satt': 'estimated_SATT'}, inplace=True)

# Load the truth file
truths_file_path = 'D:/ACIC/ACIC_estimand_truths.csv'
truths_df = pd.read_csv(truths_file_path)

# Filter to get only the year 3 SATTs for each dataset
yearly_truths_df = truths_df[(truths_df['variable']=='Yearly')&(truths_df['year'] == 3)]

# Merge the estimates with the year 3 truths
merged_df = pd.merge(estimates_df, yearly_truths_df, on='dataset.num')

# Compute the squared error and RMSE
merged_df['squared_error'] = (merged_df['estimated_SATT'] - merged_df['SATT']) ** 2
rmse = np.sqrt(merged_df['squared_error'].mean())

print(f'Overall RMSE: {rmse}')

Overall RMSE: 56.555919404890524


### Difference in Difference

####  Using (Ypost - Ypre for the treatment group) - (Ypost - Ypre for the control group) to get the treatment effect. And the treatment effect is just the SATT we're looking for?

In [9]:
# Function to estimate SATT using simple DiD approach
def estimate_satt_did_simple(index):
    merged_file = f'{output_folder}/merged_{index:04d}.csv'
    df = pd.read_csv(merged_file)
    
    # Separate pre and post intervention data
    pre_df = df[df['post'] == 0].rename(columns={'Y': 'Y_pre'})
    post_df = df[df['post'] == 1].rename(columns={'Y': 'Y_post'})
    
    # Merge pre and post data on id.practice and Z
    df_diff = pd.merge(pre_df[['id.practice', 'Z', 'Y_pre']], 
                       post_df[['id.practice', 'Z', 'Y_post']], 
                       on=['id.practice', 'Z'])
    
    # Calculate the difference in outcomes
    df_diff['Y_diff'] = df_diff['Y_post'] - df_diff['Y_pre']
    
    # Separate treated and control groups
    treated_diff = df_diff[df_diff['Z'] == 1]['Y_diff']
    control_diff = df_diff[df_diff['Z'] == 0]['Y_diff']
    
    # Calculate the treatment effect
    treatment_effect = treated_diff.mean() - control_diff.mean()
    
    return {'index': index, 'satt': treatment_effect}

output_folder = 'D:/ACIC/output'  

# Loop through all merged files and estimate SATT using simple DiD approach
results = []
for i in range(1, 3401):
    result = estimate_satt_did_simple(i)
    results.append(result)

# Save results
results_df = pd.DataFrame(results)
results_df.to_csv(f'{output_folder}/results_did_simple.csv', index=False)

print("Simple DiD calculation completed.")

Simple DiD calculation completed.


In [10]:
# Load your estimates
estimates_file_path = 'D:/ACIC/output/results_did_simple.csv'
estimates_df = pd.read_csv(estimates_file_path)

# Rename columns for clarity
estimates_df.rename(columns={'index': 'dataset.num', 'satt': 'estimated_SATT'}, inplace=True)

# Load the truth file
truths_file_path = 'D:/ACIC/ACIC_estimand_truths.csv'
truths_df = pd.read_csv(truths_file_path)

# Filter to get only the overall SATTs for each dataset
overall_truths_df = truths_df[truths_df['variable'] == 'Overall']

# Merge the estimates with the overall truths
merged_df = pd.merge(estimates_df, overall_truths_df, on='dataset.num')

# Compute the squared error and RMSE
merged_df['squared_error'] = (merged_df['estimated_SATT'] - merged_df['SATT']) ** 2
rmse = np.sqrt(merged_df['squared_error'].mean())

print(f'Overall RMSE: {rmse}')

Overall RMSE: 33.413692220594534


### DiD focus on year 2 and year 3 data

In [2]:
# Function to estimate SATT using simple DiD approach for Year 2 and Year 3 only
def estimate_satt_did(index):
    merged_file = f'{output_folder}/merged_{index:04d}.csv'
    df = pd.read_csv(merged_file)
    
    # Filter for Year 2 (pre) and Year 3 (post)
    pre_df = df[(df['post'] == 0) & (df['year'] == 2)].rename(columns={'Y': 'Y_pre'})
    post_df = df[(df['post'] == 1) & (df['year'] == 3)].rename(columns={'Y': 'Y_post'})
    
    # Merge pre and post data on id.practice and Z
    df_diff = pd.merge(pre_df[['id.practice', 'Z', 'Y_pre']], 
                       post_df[['id.practice', 'Z', 'Y_post']], 
                       on=['id.practice', 'Z'])
    
    # Calculate the difference in outcomes
    df_diff['Y_diff'] = df_diff['Y_post'] - df_diff['Y_pre']
    
    # Separate treated and control groups
    treated_diff = df_diff[df_diff['Z'] == 1]['Y_diff']
    control_diff = df_diff[df_diff['Z'] == 0]['Y_diff']
    
    # Calculate the treatment effect
    treatment_effect = treated_diff.mean() - control_diff.mean()
    
    return {'index': index, 'satt': treatment_effect}


output_folder = 'D:/ACIC/output'  

# Ensure the output folder exists
os.makedirs(output_folder, exist_ok=True)

# Loop through all merged files and estimate SATT using simple DiD approach
results = []
for i in range(1, 3401):
    result = estimate_satt_did(i)
    results.append(result)

# Save results
results_df = pd.DataFrame(results)
results_df.to_csv(f'{output_folder}/results_did_year2_year3.csv', index=False)

print("Simple DiD calculation for Year 2 and Year 3 completed.")


Simple DiD calculation for Year 2 and Year 3 completed.


In [8]:
# Load your estimates
estimates_file_path = 'D:/ACIC/output/results_did_year2_year3.csv'
estimates_df = pd.read_csv(estimates_file_path)

# Rename columns for clarity
estimates_df.rename(columns={'index': 'dataset.num', 'satt': 'estimated_SATT'}, inplace=True)

# Load the truth file
truths_file_path = 'D:/ACIC/ACIC_estimand_truths.csv'
truths_df = pd.read_csv(truths_file_path)

# Filter to get only the year 3 SATTs for each dataset
yearly_truths_df = truths_df[(truths_df['variable']=='Yearly')&(truths_df['year'] == 3)]

# Merge the estimates with the year 3 truths
merged_df = pd.merge(estimates_df, yearly_truths_df, on='dataset.num')

# Compute the squared error and RMSE
merged_df['squared_error'] = (merged_df['estimated_SATT'] - merged_df['SATT']) ** 2
rmse = np.sqrt(merged_df['squared_error'].mean())

print(f'Overall RMSE: {rmse}')

Overall RMSE: 22.650375994668043


###  DiD with IPTW

In [5]:
# Function to estimate SATT using DiD with linear regression and IPTW
def estimate_satt_did_iptw(index):
    merged_file = f'{output_folder}/merged_{index:04d}.csv'
    df = pd.read_csv(merged_file)
    
    # Filter for Year 2 (pre) and Year 3 (post)
    pre_df = df[(df['post'] == 0) & (df['year'] == 2)].copy()
    post_df = df[(df['post'] == 1) & (df['year'] == 3)].copy()
    
    # Merge pre and post data on id.practice and Z
    df_diff = pd.merge(pre_df[['id.practice', 'Z', 'Y']], 
                       post_df[['id.practice', 'Z', 'Y']], 
                       on=['id.practice', 'Z'], suffixes=('_pre', '_post'))
    
    # Calculate the difference in outcomes
    df_diff['Y_diff'] = df_diff['Y_post'] - df_diff['Y_pre']
    
    # One-hot encode categorical variables
    df = pd.get_dummies(df, columns=['X2', 'X4'], drop_first=True)
    pre_df = pd.get_dummies(pre_df, columns=['X2', 'X4'], drop_first=True)
    post_df = pd.get_dummies(post_df, columns=['X2', 'X4'], drop_first=True)
    
    # Ensure the columns in pre_df and post_df are the same
    pre_df, post_df = pre_df.align(post_df, join='inner', axis=1)
    
    # Define features and treatment
    X = df.drop(columns=['Y', 'id.practice', 'year', 'Z', 'post'])
    T = df['Z']
    y = df['Y']
    
    # Standardize the features
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X)
    
    # Estimate propensity scores using logistic regression
    prop_model = LogisticRegression(max_iter=1000)
    prop_model.fit(X_scaled, T)
    propensity_scores = prop_model.predict_proba(X_scaled)[:, 1]
    
    # Calculate weights for IPTW
    weights = T / propensity_scores + (1 - T) / (1 - propensity_scores)
    
    # Extract covariates for pre-intervention period
    X_pre = pre_df.drop(columns=['Y', 'id.practice', 'Z', 'year', 'post'])
    X_post = post_df.drop(columns=['Y', 'id.practice', 'Z', 'year', 'post'])
    
    # Standardize the covariates
    X_pre_scaled = scaler.fit_transform(X_pre)
    X_post_scaled = scaler.transform(X_post)
    
    # Create interaction terms
    X_diff = np.concatenate([X_pre_scaled, X_post_scaled], axis=1)
    
    # Ensure weights are correctly aligned with the pre_df index
    weights_pre = weights[pre_df.index]
    
    # Train weighted linear regression model on the difference in outcomes
    model_diff = LinearRegression().fit(X_diff, df_diff['Y_diff'], sample_weight=weights_pre)
    
    # Predict the treatment effect
    df_diff['Y_diff_pred'] = model_diff.predict(X_diff)
    
    # Separate treated and control groups
    treated_diff = df_diff[df_diff['Z'] == 1]['Y_diff_pred']
    control_diff = df_diff[df_diff['Z'] == 0]['Y_diff_pred']
    
    # Calculate the treatment effect
    treatment_effect = treated_diff.mean() - control_diff.mean()
    
    return {'index': index, 'satt': treatment_effect}

# Loop through all merged files and estimate SATT using DiD with IPTW
results = []
for i in range(1, 3401):
    result = estimate_satt_did_iptw(i)
    results.append(result)

# Save SATT results
results_df = pd.DataFrame(results)
results_df.to_csv(f'{output_folder}/satt_results_did_iptw.csv', index=False)

print("DiD with IPTW model development and SATT estimation completed.")

DiD with IPTW model development and SATT estimation completed.


In [6]:
# Load your estimates
estimates_file_path = 'D:/ACIC/output/satt_results_did_iptw.csv'
estimates_df = pd.read_csv(estimates_file_path)

# Rename columns for clarity
estimates_df.rename(columns={'index': 'dataset.num', 'satt': 'estimated_SATT'}, inplace=True)

# Load the truth file
truths_file_path = 'D:/ACIC/ACIC_estimand_truths.csv'
truths_df = pd.read_csv(truths_file_path)

# Filter to get only the year 3 SATTs for each dataset
yearly_truths_df = truths_df[(truths_df['variable']=='Yearly')&(truths_df['year'] == 3)]

# Merge the estimates with the year 3 truths
merged_df = pd.merge(estimates_df, yearly_truths_df, on='dataset.num')

# Compute the squared error and RMSE
merged_df['squared_error'] = (merged_df['estimated_SATT'] - merged_df['SATT']) ** 2
rmse = np.sqrt(merged_df['squared_error'].mean())

print(f'Overall RMSE: {rmse}')

Overall RMSE: 28.489106391630614
